# Novos casos positivos em Itália #

> Neste notebook estão presentes 3 mapas relativos aos novos casos positivos de covid-19 em Itália em três datas diferentes. Todos os dados foram retirados de https://github.com/pcm-dpc/COVID-19.

## Ligação ao Qgis ##

In [1]:
import os
import sys
from osgeo import ogr
os.environ['QT_QPA_PLATFORM'] = 'offscreen'
sys.path.insert(0,'/usr/local/share/qgis/python')
from qgis.core import *
QgsApplication.setPrefixPath("/usr/local", True) 
from qgis.gui import *
from qgis import processing
from IPython.display import Image
from qgis.PyQt.QtGui import QColor, QImage
from qgis.PyQt.QtCore import QSize, QBuffer, QIODevice
from qgis.utils import iface
from qgis.core import *
from qgis.PyQt.QtGui import *
from qgis.PyQt.QtCore import *

qgs = QgsApplication([], True)
qgs.initQgis()
print(QgsApplication.showSettings())
project = QgsProject.instance()

Application state:
QGIS_PREFIX_PATH env var:		/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS
Prefix:		/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS
Plugin Path:		/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../PlugIns/qgis
Package Data Path:	/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../Resources
Active Theme Name:	
Active Theme Path:	/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../Resources/resources/themes//icons/
Default Theme Path:	:/images/themes/default/
SVG Search Paths:	/usr/local/../Resources/svg/
		/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../Resources/svg/
		/Users/dianamartins/Library/Application Support/profiles/default/svg/
User DB Path:	/Users/dianamartins/anaconda3/QGIS.app/Contents/MacOS/../Resources/resources/qgis.db
Auth DB Path:	/Users/dianamartins/Library/Application Support/profiles/default/qgis-auth.db



## - Novos casos positivos em 24 de fevereiro de 2020 ##

### Carregamento de uma shapefile que define as regiões de Itália ###

In [ ]:
italy_map = "/Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Dados/ITA_adm/ITA_adm1.shp"
vlayer = QgsVectorLayer(italy_map, "italy_map", "ogr")
if not vlayer.isValid():
    print("Layer failed to load!")
else:
    QgsProject.instance().addMapLayer(vlayer)
    print("Layer loaded!")

### Carregamento do csv com os dados relativos à covid-19 em Itália ###

In [3]:
csv_path = "file:///Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Dados/casos_italia_atual.csv?delimiter=,"
csv_layer = QgsVectorLayer(csv_path, 'Data', 'delimitedtext')

if not csv_layer.isValid():
    print('Layer failed to load!')
else:
    QgsProject.instance().addMapLayer(csv_layer)
    print("Layer loaded !")

Layer loaded !


### Juntar as camadas da shapefile e do csv ###

> Estas duas camadas vão ser juntadas através dos atributos "codice_regione" e "ID_1".

In [4]:
joinName='codice_regione'
targetName='ID_1'

joinObject=QgsVectorLayerJoinInfo()
joinObject.setJoinFieldName(joinName)
joinObject.setTargetFieldName(targetName)
joinObject.setJoinLayerId(csv_layer.id())
joinObject.setUsingMemoryCache(True)
joinObject.setJoinLayer(csv_layer)
flag = vlayer.addJoin(joinObject)



In [5]:
novospositivos_layer = vlayer.clone()
novospositivos_layer.setName("Novos positivos")

for field in novospositivos_layer.fields():
    print("Column "+field.name()+" Load")

Column ID_0 Load
Column ISO Load
Column NAME_0 Load
Column ID_1 Load
Column NAME_1 Load
Column TYPE_1 Load
Column ENGTYPE_1 Load
Column NL_NAME_1 Load
Column VARNAME_1 Load
Column Data_data Load
Column Data_stato Load
Column Data_denominazione_regione Load
Column Data_lat Load
Column Data_long Load
Column Data_ricoverati_con_sintomi Load
Column Data_terapia_intensiva Load
Column Data_totale_ospedalizzati Load
Column Data_isolamento_domiciliare Load
Column Data_totale_positivi Load
Column Data_variazione_totale_positivi Load
Column Data_nuovi_positivi Load
Column Data_dimessi_guariti Load
Column Data_deceduti Load
Column Data_totale_casi Load
Column Data_tamponi Load
Column Data_casi_testati Load
Column Data_note_it Load
Column Data_note_en Load


### Simbologia para o mapa dos novos casos positivos ###

In [29]:
label_settings = QgsPalLayerSettings()
label_settings.drawBackground = True
label_settings.fieldName = "NAME_1"

text_format = QgsTextFormat()
text_format.setFont(QFont("Arial", 10))
text_format.setSize(55) 

background_color = QgsTextBackgroundSettings()
background_color.setEnabled(False)

text_format.setBackground(background_color )
label_settings.setFormat(text_format)

novospositivos_layer.setLabeling(QgsVectorLayerSimpleLabeling(label_settings))
novospositivos_layer.setLabelsEnabled(True)
novospositivos_layer.triggerRepaint()


In [30]:
from qgis.PyQt import QtGui


myOpacity = 1
myTargetField = 'Data_nuovi_positivi'
myRangeList = []

myMin = 0
myMax = 0
myLabel = '0-0'
myColour = QtGui.QColor('#ffffff')
mySymbol = QgsSymbol.defaultSymbol(novospositivos_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 0
myMax = 10
myLabel = '0 - 10'
myColour = QtGui.QColor('#3ADF00')
mySymbol = QgsSymbol.defaultSymbol(novospositivos_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 10
myMax = 30
myLabel = '10 - 30'
myColour = QtGui.QColor('#088A08')
mySymbol = QgsSymbol.defaultSymbol(novospositivos_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 30
myMax = 50
myLabel = '30 - 50'
myColour = QtGui.QColor('#075e0e')
mySymbol = QgsSymbol.defaultSymbol(novospositivos_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 50
myMax = 100
myLabel = '50 - 100'
myColour = QtGui.QColor('#122A0A')
mySymbol = QgsSymbol.defaultSymbol(novospositivos_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 100
myMax = 400
myLabel = '100 - 400'
myColour = QtGui.QColor('#122A0A')
mySymbol = QgsSymbol.defaultSymbol(novospositivos_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myRenderer = QgsGraduatedSymbolRenderer('', myRangeList)
myClassificationMethod = QgsApplication.classificationMethodRegistry().method("EqualInterval")
myRenderer.setClassificationMethod(myClassificationMethod)
myRenderer.setClassAttribute(myTargetField)

novospositivos_layer.setRenderer(myRenderer)



In [31]:
xt = novospositivos_layer.extent()
width  = 1024
height = int(width*xt.height()/xt.width())

project = QgsProject().instance()
project.addMapLayers([novospositivos_layer])
manager = project.layoutManager()
layoutName = 'novos_casos'
layouts_list = manager.printLayouts()
for layout in layouts_list:
    if layout.name() == layoutName:
        manager.removeLayout(layout)
        
layout = QgsPrintLayout(project)
layout.initializeDefaults()
layout.setName(layoutName)
manager.addLayout(layout)

pc = layout.pageCollection()
pc.page(0).attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))


map = QgsLayoutItemMap(layout)
map.setRect(20,20,20,20)
map.setLayers([novospositivos_layer])

ms = QgsMapSettings()
ms.setLayers([novospositivos_layer])
ms.setExtent(xt)
map.setExtent(xt)

layout.addLayoutItem(map)

map.attemptMove(QgsLayoutPoint(0,0,QgsUnitTypes.LayoutMillimeters))
map.attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))

map.setBackgroundColor(QColor(230, 234, 238))

legend = QgsLayoutItemLegend(layout)
legend.setReferencePoint(6)
legend.setScale(3)
legend.attemptMove(QgsLayoutPoint(0,height,QgsUnitTypes.LayoutMillimeters))

layout.addLayoutItem(legend)
legend.setLegendFilterByMapEnabled(True)
legend.setLinkedMap(map)

exporter = QgsLayoutExporter(manager.layoutByName("novos_casos"))

image = exporter.renderPageToImage(0)
image = exporter.renderPageToImage(0)

from IPython.display import Image
imgbuf= QBuffer()
imgbuf.open( QIODevice.ReadWrite )
image.save( imgbuf,"PNG" )
image.save('/Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Imagens/novos_casosatual',"PNG")
Image( imgbuf.data() )

## - Novos casos positivos em 29 de maio de 2020 ##

In [9]:
italy_map = "/Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Dados/ITA_adm/ITA_adm1.shp"
vlayer = QgsVectorLayer(italy_map, "italy_map", "ogr")
if not vlayer.isValid():
    print("Layer failed to load!")
else:
    QgsProject.instance().addMapLayer(vlayer)
    print("Layer loaded!")

Layer loaded!


In [10]:
csv_path = "file:///Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Dados/casos_italia_inicio.csv?delimiter=,"
csv_layer = QgsVectorLayer(csv_path, 'Data', 'delimitedtext')

if not csv_layer.isValid():
    print('Layer failed to load!')
else:
    QgsProject.instance().addMapLayer(csv_layer)
    print("Layer loaded !")

Layer loaded !


In [11]:
joinName='codice_regione'
targetName='ID_1'

joinObject=QgsVectorLayerJoinInfo()
joinObject.setJoinFieldName(joinName)
joinObject.setTargetFieldName(targetName)
joinObject.setJoinLayerId(csv_layer.id())
joinObject.setUsingMemoryCache(True)
joinObject.setJoinLayer(csv_layer)
flag = vlayer.addJoin(joinObject)

In [12]:
novospositivosinicio_layer = vlayer.clone()
novospositivosinicio_layer.setName("Novos positivos")

for field in novospositivosinicio_layer.fields():
    print("Column "+field.name()+" Load")

Column ID_0 Load
Column ISO Load
Column NAME_0 Load
Column ID_1 Load
Column NAME_1 Load
Column TYPE_1 Load
Column ENGTYPE_1 Load
Column NL_NAME_1 Load
Column VARNAME_1 Load
Column Data_data Load
Column Data_stato Load
Column Data_denominazione_regione Load
Column Data_lat Load
Column Data_long Load
Column Data_ricoverati_con_sintomi Load
Column Data_terapia_intensiva Load
Column Data_totale_ospedalizzati Load
Column Data_isolamento_domiciliare Load
Column Data_totale_positivi Load
Column Data_variazione_totale_positivi Load
Column Data_nuovi_positivi Load
Column Data_dimessi_guariti Load
Column Data_deceduti Load
Column Data_totale_casi Load
Column Data_tamponi Load
Column Data_casi_testati Load
Column Data_note_it Load
Column Data_note_en Load


In [32]:
label_settings = QgsPalLayerSettings()
label_settings.drawBackground = True
label_settings.fieldName = "NAME_1"

text_format = QgsTextFormat()
text_format.setFont(QFont("Arial", 10))
text_format.setSize(55) 

background_color = QgsTextBackgroundSettings()
background_color.setEnabled(False)

text_format.setBackground(background_color )
label_settings.setFormat(text_format)

novospositivosinicio_layer.setLabeling(QgsVectorLayerSimpleLabeling(label_settings))
novospositivosinicio_layer.setLabelsEnabled(True)
novospositivosinicio_layer.triggerRepaint()

In [33]:
from qgis.PyQt import QtGui


myOpacity = 1
myTargetField = 'Data_nuovi_positivi'
myRangeList = []

myMin = 0
myMax = 0
myLabel = '0-0'
myColour = QtGui.QColor('#ffffff')
mySymbol = QgsSymbol.defaultSymbol(novospositivosinicio_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 0
myMax = 10
myLabel = '0 - 10'
myColour = QtGui.QColor('#ffffcc')
mySymbol = QgsSymbol.defaultSymbol(novospositivosinicio_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 10
myMax = 30
myLabel = '10 - 30'
myColour = QtGui.QColor('#ffff99')
mySymbol = QgsSymbol.defaultSymbol(novospositivosinicio_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 30
myMax = 50
myLabel = '30 - 50'
myColour = QtGui.QColor('#ffff66')
mySymbol = QgsSymbol.defaultSymbol(novospositivosinicio_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 50
myMax = 100
myLabel = '50 - 100'
myColour = QtGui.QColor('#ffff00')
mySymbol = QgsSymbol.defaultSymbol(novospositivosinicio_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 100
myMax = 200
myLabel = '100 - 200'
myColour = QtGui.QColor('#cc9900')
mySymbol = QgsSymbol.defaultSymbol(novospositivosinicio_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myRenderer = QgsGraduatedSymbolRenderer('', myRangeList)
myClassificationMethod = QgsApplication.classificationMethodRegistry().method("EqualInterval")
myRenderer.setClassificationMethod(myClassificationMethod)
myRenderer.setClassAttribute(myTargetField)

novospositivosinicio_layer.setRenderer(myRenderer)


In [34]:
xt = novospositivosinicio_layer.extent()
width  = 1024
height = int(width*xt.height()/xt.width())

project = QgsProject().instance()
project.addMapLayers([novospositivosinicio_layer])
manager = project.layoutManager()
layoutName = 'novos_casos_inicio'
layouts_list = manager.printLayouts()
for layout in layouts_list:
    if layout.name() == layoutName:
        manager.removeLayout(layout)
        
layout = QgsPrintLayout(project)
layout.initializeDefaults()
layout.setName(layoutName)
manager.addLayout(layout)

pc = layout.pageCollection()
pc.page(0).attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))


map = QgsLayoutItemMap(layout)
map.setRect(20,20,20,20)
map.setLayers([novospositivosinicio_layer])

ms = QgsMapSettings()
ms.setLayers([novospositivosinicio_layer])
ms.setExtent(xt)
map.setExtent(xt)

layout.addLayoutItem(map)

map.attemptMove(QgsLayoutPoint(0,0,QgsUnitTypes.LayoutMillimeters))
map.attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))

map.setBackgroundColor(QColor(230, 234, 238))

legend = QgsLayoutItemLegend(layout)
legend.setReferencePoint(6)
legend.setScale(3)
legend.attemptMove(QgsLayoutPoint(0,height,QgsUnitTypes.LayoutMillimeters))

layout.addLayoutItem(legend)
legend.setLegendFilterByMapEnabled(True)
legend.setLinkedMap(map)

exporter = QgsLayoutExporter(manager.layoutByName("novos_casos_inicio"))

image = exporter.renderPageToImage(0)
image = exporter.renderPageToImage(0)

from IPython.display import Image
imgbuf= QBuffer()
imgbuf.open( QIODevice.ReadWrite )
image.save( imgbuf,"PNG" )
image.save('/Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Imagens/novos_casos_inicio',"PNG")
Image( imgbuf.data() )

## - Novos casos positivos em 23 de março de 2020 ##

In [16]:
italy_map = "/Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Dados/ITA_adm/ITA_adm1.shp"
vlayer = QgsVectorLayer(italy_map, "italy_map", "ogr")
if not vlayer.isValid():
    print("Layer failed to load!")
else:
    QgsProject.instance().addMapLayer(vlayer)
    print("Layer loaded!")

Layer loaded!


In [17]:
csv_path = "file:///Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Dados/casos_italia_23marco.csv?delimiter=,"
csv_layer = QgsVectorLayer(csv_path, 'Data', 'delimitedtext')

if not csv_layer.isValid():
    print('Layer failed to load!')
else:
    QgsProject.instance().addMapLayer(csv_layer)
    print("Layer loaded !")

Layer loaded !


In [18]:
joinName='codice_regione'
targetName='ID_1'

joinObject=QgsVectorLayerJoinInfo()
joinObject.setJoinFieldName(joinName)
joinObject.setTargetFieldName(targetName)
joinObject.setJoinLayerId(csv_layer.id())
joinObject.setUsingMemoryCache(True)
joinObject.setJoinLayer(csv_layer)
flag = vlayer.addJoin(joinObject)

In [19]:
novospositivosmarco_layer = vlayer.clone()
novospositivosmarco_layer.setName("Novos positivos")

for field in novospositivosmarco_layer.fields():
    print("Column "+field.name()+" Load")

Column ID_0 Load
Column ISO Load
Column NAME_0 Load
Column ID_1 Load
Column NAME_1 Load
Column TYPE_1 Load
Column ENGTYPE_1 Load
Column NL_NAME_1 Load
Column VARNAME_1 Load
Column Data_data Load
Column Data_stato Load
Column Data_denominazione_regione Load
Column Data_lat Load
Column Data_long Load
Column Data_ricoverati_con_sintomi Load
Column Data_terapia_intensiva Load
Column Data_totale_ospedalizzati Load
Column Data_isolamento_domiciliare Load
Column Data_totale_positivi Load
Column Data_variazione_totale_positivi Load
Column Data_nuovi_positivi Load
Column Data_dimessi_guariti Load
Column Data_deceduti Load
Column Data_totale_casi Load
Column Data_tamponi Load
Column Data_casi_testati Load
Column Data_note_it Load
Column Data_note_en Load


In [35]:
label_settings = QgsPalLayerSettings()
label_settings.drawBackground = True
label_settings.fieldName = "NAME_1"

text_format = QgsTextFormat()
text_format.setFont(QFont("Arial", 10))
text_format.setSize(55) 

background_color = QgsTextBackgroundSettings()
background_color.setEnabled(False)

text_format.setBackground(background_color )
label_settings.setFormat(text_format)

novospositivosmarco_layer.setLabeling(QgsVectorLayerSimpleLabeling(label_settings))
novospositivosmarco_layer.setLabelsEnabled(True)
novospositivosmarco_layer.triggerRepaint()

In [36]:
from qgis.PyQt import QtGui


myOpacity = 1
myTargetField = 'Data_nuovi_positivi'
myRangeList = []

myMin = 0
myMax = 0
myLabel = '0-0'
myColour = QtGui.QColor('#ffffff')
mySymbol = QgsSymbol.defaultSymbol(novospositivosmarco_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 0
myMax = 100
myLabel = '0 - 100'
myColour = QtGui.QColor('#ffcccc')
mySymbol = QgsSymbol.defaultSymbol(novospositivosmarco_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 100
myMax = 200
myLabel = '100 - 200'
myColour = QtGui.QColor('#ffb3b3')
mySymbol = QgsSymbol.defaultSymbol(novospositivosmarco_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 200
myMax = 300
myLabel = '200 - 300'
myColour = QtGui.QColor('#ff9999')
mySymbol = QgsSymbol.defaultSymbol(novospositivosmarco_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 300
myMax = 400
myLabel = '300 - 400'
myColour = QtGui.QColor('#ff6666')
mySymbol = QgsSymbol.defaultSymbol(novospositivosmarco_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 400
myMax = 1000
myLabel = '400 - 1000'
myColour = QtGui.QColor('#e60000')
mySymbol = QgsSymbol.defaultSymbol(novospositivosmarco_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myMin = 1000
myMax = 1800
myLabel = '1000 - 1800'
myColour = QtGui.QColor('#b30000')
mySymbol = QgsSymbol.defaultSymbol(novospositivosmarco_layer.geometryType())
mySymbol.setColor(myColour)
myRange = QgsRendererRange(myMin, myMax, mySymbol, myLabel)
myRangeList.append(myRange)

myRenderer = QgsGraduatedSymbolRenderer('', myRangeList)
myClassificationMethod = QgsApplication.classificationMethodRegistry().method("EqualInterval")
myRenderer.setClassificationMethod(myClassificationMethod)
myRenderer.setClassAttribute(myTargetField)

novospositivosmarco_layer.setRenderer(myRenderer)


In [ ]:
xt = novospositivosinicio_layer.extent()
width  = 1024
height = int(width*xt.height()/xt.width())

project = QgsProject().instance()
project.addMapLayers([novospositivosmarco_layer])
manager = project.layoutManager()
layoutName = 'novos_casos_23marco'
layouts_list = manager.printLayouts()
for layout in layouts_list:
    if layout.name() == layoutName:
        manager.removeLayout(layout)
        
layout = QgsPrintLayout(project)
layout.initializeDefaults()
layout.setName(layoutName)
manager.addLayout(layout)

pc = layout.pageCollection()
pc.page(0).attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))


map = QgsLayoutItemMap(layout)
map.setRect(20,20,20,20)
map.setLayers([novospositivosmarco_layer])

ms = QgsMapSettings()
ms.setLayers([novospositivosmarco_layer])
ms.setExtent(xt)
map.setExtent(xt)

layout.addLayoutItem(map)

map.attemptMove(QgsLayoutPoint(0,0,QgsUnitTypes.LayoutMillimeters))
map.attemptResize(QgsLayoutSize(width,height,QgsUnitTypes.LayoutMillimeters))

map.setBackgroundColor(QColor(230, 234, 238))

legend = QgsLayoutItemLegend(layout)
legend.setReferencePoint(6)
legend.setScale(3)
legend.attemptMove(QgsLayoutPoint(0,height,QgsUnitTypes.LayoutMillimeters))

layout.addLayoutItem(legend)
legend.setLegendFilterByMapEnabled(True)
legend.setLinkedMap(map)

exporter = QgsLayoutExporter(manager.layoutByName("novos_casos_23marco"))

image = exporter.renderPageToImage(0)
image = exporter.renderPageToImage(0)

from IPython.display import Image
imgbuf= QBuffer()
imgbuf.open( QIODevice.ReadWrite )
image.save( imgbuf,"PNG" )
image.save('/Users/dianamartins/Documents/GitHub/Epidemiologia/Trabalho_final/Imagens/novos_casos_23marco',"PNG")
Image( imgbuf.data() )